In [18]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!pip install geopy

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.4.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


In [19]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


In [20]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

In [21]:
neighborhoods_data = newyork_data['features']
neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

In [22]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

In [23]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [24]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


In [25]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [26]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [27]:
CLIENT_ID = '4DML2HSAO45JC0PEDAPHGYK0J5DQKOKV0S32IDNXZOPPGTTL' # your Foursquare ID
CLIENT_SECRET = 'GNEMFRZYQ4UMZOBIACOP0D4GP33ZJK0WCPYR2KQ5Q44K0X5J' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 4DML2HSAO45JC0PEDAPHGYK0J5DQKOKV0S32IDNXZOPPGTTL
CLIENT_SECRET:GNEMFRZYQ4UMZOBIACOP0D4GP33ZJK0WCPYR2KQ5Q44K0X5J


In [28]:
neighborhood_latitude = neighborhoods.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = neighborhoods.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = neighborhoods.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Wakefield are 40.89470517661, -73.84720052054902.


In [29]:
LIMIT = 100
radius = 500
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url

'https://api.foursquare.com/v2/venues/explore?&client_id=4DML2HSAO45JC0PEDAPHGYK0J5DQKOKV0S32IDNXZOPPGTTL&client_secret=GNEMFRZYQ4UMZOBIACOP0D4GP33ZJK0WCPYR2KQ5Q44K0X5J&v=20180605&ll=40.89470517661,-73.84720052054902&radius=500&limit=100'

In [30]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5f11ea58af2b4b3137e13795'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Wakefield',
  'headerFullLocation': 'Wakefield, Bronx',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 11,
  'suggestedBounds': {'ne': {'lat': 40.899205181110005,
    'lng': -73.84125857127495},
   'sw': {'lat': 40.89020517211, 'lng': -73.8531424698231}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4c537892fd2ea593cb077a28',
       'name': 'Lollipops Gelato',
       'location': {'address': '4120 Baychester Ave',
        'crossStreet': 'Edenwald & Bussing Ave',
        'lat': 40.894123150205274,
        'lng': -73.84589162362325,
        'labeledLatL

In [31]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [32]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  This is separate from the ipykernel package so we can avoid doing imports until


name      categories        lat        lng
0  Lollipops Gelato    Dessert Shop  40.894123 -73.845892
1         Walgreens        Pharmacy  40.896528 -73.844700
2  Carvel Ice Cream  Ice Cream Shop  40.890487 -73.848568
3          Rite Aid        Pharmacy  40.896649 -73.844846
4           Dunkin'      Donut Shop  40.890459 -73.849089

In [33]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

11 venues were returned by Foursquare.


In [34]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [35]:
newyork_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [36]:
print(newyork_venues.shape)
newyork_venues.head()

(10120, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1         Walgreens       40.896528       -73.844700        Pharmacy  
2  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
3          Rite Aid       40.896649       -73.844846        Pharmacy  
4           Dunkin'       40.890459       -73.849089      Donut Shop

In [37]:
newyork_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                      29                      29   
Annadale                                      12                      12   
Arden Heights                                  5                       5   
Arlington                                      4                       4   
Arrochar                                      22                      22   
Arverne                                       19                      19   
Astoria                                       99                      99   
Astoria Heights                               13                      13   
Auburndale                                    20                      20   
Bath Beach                                    47                      47   
Battery Park City                             68                      68   
Bay Ridge                                     81                      81   
Bay Terrace                                   46                      46   
Baychester                                    20                      20   
Bayside                                       74                      74   
Bayswater                                      2                       2   
Bedford Park                                  36                      36   
Bedford Stuyvesant                            26                      26   
Beechhurst                                    15                      15   
Bellaire                                      13                      13   
Belle Harbor                                  17                      17   
Bellerose                                     21                      21   
Belmont                                       96                      96   
Bensonhurst                                   31                      31   
Bergen Beach                                   6                       6   
Blissville                                    16                      16   
Bloomfield                                     4                       4   
Boerum Hill                                   90                      90   
Borough Park                                  21                      21   
Breezy Point                                   5                       5   
Briarwood                                     11                      11   
Brighton Beach                                44                      44   
Broad Channel                                  5                       5   
Broadway Junction                             15                      15   
Bronxdale                                     12                      12   
Brooklyn Heights                             100                     100   
Brookville                                     1                       1   
Brownsville                                   19                      19   
Bulls Head                                    43                      43   
Bushwick                                      72                      72   
Butler Manor                                   6                       6   
Cambria Heights                               12                      12   
Canarsie                                       4                       4   
Carnegie Hill                                 95                      95   
Carroll Gardens                              100                     100   
Castle Hill                                    8                       8   
Castleton Corners                             15                      15   
Central Harlem                                44                      44   
Charleston                                    29                      29   
Chelsea                                      106                     106   
Chinatown                                    100                     100   

In [38]:
print('There are {} uniques categories.'.format(len(newyork_venues['Venue Category'].unique())))

There are 428 uniques categories.


In [39]:
# one hot encoding
newyork_onehot = pd.get_dummies(newyork_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
newyork_onehot['Neighborhood'] = newyork_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [newyork_onehot.columns[-1]] + list(newyork_onehot.columns[:-1])
newyork_onehot = newyork_onehot[fixed_columns]

newyork_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  \
0            0                  0               0                  0   
1            0                  0               0                  0   
2            0                  0               0                  0   
3            0                  0               0                  0   
4            0                  0               0                  0   

   African Restaurant  American Restaurant  Antique Shop  Arcade  \
0                   0                    0             0       0   
1                   0                    0             0       0   
2                   0                    0             0       0   
3                   0                    0             0       0   
4                   0                    0             0       0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0                 0                       0            0           0   
1                 0                       0            0           0   
2                 0                       0            0           0   
3                 0                       0            0           0   
4                 0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   Auto Dealership  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  \
0                0                0          0           0           0   
1                0                0          0           0           0   
2                0                0          0           0           0   
3                0                0          0           0           0   
4                0                0          0           0           0   

   Bakery  Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0       0     0    0               0                 0                 0   
1       0     0    0               0                 0                 0   
2       0     0    0               0                 0                 0   
3       0     0    0               0                 0                 0   
4       0     0    0               0                 0                 0   

   Bath House  Beach  Beach Bar  Bed & Breakfast  Beer Bar  Beer Garden  \
0           0      0          0                0         0            0   
1           0      0          0                0         0            0   
2           0      0          0                0         0            0   
3           0      0          0                0         0            0   
4           0      0          0                0         0            0   

   Beer Store  Big Box Store  Bike Rental / Bike Share  Bike Shop  Bike Trail  \
0           0              0                         0          0           0   
1           0              0                         0          0           0   
2           0              0                         0          0           0   
3           0              0                         0          0           0   
4           0              0                         0          0           0   

   B

In [40]:
newyork_onehot.shape

(10120, 428)

In [41]:
newyork_grouped = newyork_onehot.groupby('Neighborhood').mean().reset_index()
newyork_grouped

Neighborhood  Yoga Studio  Accessories Store  \
0                     Allerton     0.000000           0.000000   
1                     Annadale     0.000000           0.000000   
2                Arden Heights     0.000000           0.000000   
3                    Arlington     0.000000           0.000000   
4                     Arrochar     0.000000           0.000000   
5                      Arverne     0.000000           0.000000   
6                      Astoria     0.000000           0.000000   
7              Astoria Heights     0.000000           0.000000   
8                   Auburndale     0.000000           0.000000   
9                   Bath Beach     0.000000           0.000000   
10           Battery Park City     0.000000           0.000000   
11                   Bay Ridge     0.000000           0.000000   
12                 Bay Terrace     0.000000           0.021739   
13                  Baychester     0.000000           0.000000   
14                     Bayside     0.013514           0.000000   
15                   Bayswater     0.000000           0.000000   
16                Bedford Park     0.000000           0.000000   
17          Bedford Stuyvesant     0.000000           0.000000   
18                  Beechhurst     0.066667           0.000000   
19                    Bellaire     0.000000           0.000000   
20                Belle Harbor     0.000000           0.000000   
21                   Bellerose     0.000000           0.000000   
22                     Belmont     0.000000           0.000000   
23                 Bensonhurst     0.000000           0.000000   
24                Bergen Beach     0.000000           0.000000   
25                  Blissville     0.000000           0.000000   
26                  Bloomfield     0.000000           0.000000   
27                 Boerum Hill     0.022222           0.000000   
28                Borough Park     0.000000           0.000000   
29                Breezy Point     0.000000           0.000000   
30                   Briarwood     0.000000           0.000000   
31              Brighton Beach     0.000000           0.000000   
32               Broad Channel     0.000000           0.000000   
33           Broadway Junction     0.000000           0.000000   
34                   Bronxdale     0.000000           0.000000   
35            Brooklyn Heights     0.040000           0.000000   
36                  Brookville     0.000000           0.000000   
37                 Brownsville     0.000000           0.000000   
38                  Bulls Head     0.000000           0.000000   
39                    Bushwick     0.000000           0.000000   
40                Butler Manor     0.000000           0.000000   
41             Cambria Heights     0.000000           0.000000   
42                    Canarsie     0.000000           0.000000   
43               Carnegie Hill     0.031579           0.000000   
44             Carroll Gardens     0.000000           0.000000   
45                 Castle Hill     0.000000           0.000000   
46           Castleton Corners     0.000000           0.000000   
47              Central Harlem     0.000000           0.000000   
48                  Charleston     0.000000           0.000000   
49                     Chelsea     0.000000           0.000000   
50                   Chinatown     0.010000           0.000000   
51                 City Island     0.000000           0.000000   
52                   City Line     0.000000           0.000000   
53                Civic Center     0.030000           0.000000   
54           Claremont Village     0.000000           0.000000   
55                Clason Point     0.000000           0.000000   
56                     Clifton     0.000000           0.000000   
57                     Clinton     0.000000           0.000000   
58                Clinton Hill     0.031579           0.000000   
59                  Co-op City     0.000000           0.00

In [42]:
newyork_grouped.shape

(302, 428)

In [43]:
num_top_venues = 5

for hood in newyork_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = newyork_grouped[newyork_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Allerton----
               venue  freq
0      Deli / Bodega  0.14
1        Pizza Place  0.14
2   Department Store  0.07
3        Supermarket  0.07
4  Martial Arts Dojo  0.03


----Annadale----
                 venue  freq
0  American Restaurant  0.17
1          Pizza Place  0.17
2           Restaurant  0.08
3             Pharmacy  0.08
4                Diner  0.08


----Arden Heights----
           venue  freq
0  Deli / Bodega   0.2
1       Pharmacy   0.2
2       Bus Stop   0.2
3    Coffee Shop   0.2
4    Pizza Place   0.2


----Arlington----
                 venue  freq
0        Deli / Bodega  0.25
1        Grocery Store  0.25
2  American Restaurant  0.25
3         Intersection  0.25
4   Persian Restaurant  0.00


----Arrochar----
                venue  freq
0  Italian Restaurant  0.09
1          Bagel Shop  0.09
2       Deli / Bodega  0.09
3         Pizza Place  0.09
4        Liquor Store  0.09


----Arverne----
            venue  freq
0       Surf Spot  0.21
1   Metro Station  

In [44]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [45]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = newyork_grouped['Neighborhood']

for ind in np.arange(newyork_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(newyork_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Allerton         Deli / Bodega           Pizza Place   
1       Annadale           Pizza Place   American Restaurant   
2  Arden Heights         Deli / Bodega              Bus Stop   
3      Arlington          Intersection         Deli / Bodega   
4       Arrochar    Italian Restaurant              Bus Stop   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0      Department Store           Supermarket              Pharmacy   
1          Dance Studio        Cosmetics Shop          Liquor Store   
2           Coffee Shop              Pharmacy           Pizza Place   
3   American Restaurant         Grocery Store         Women's Store   
4         Deli / Bodega          Liquor Store           Pizza Place   

  6th Most Common Venue       7th Most Common Venue 8th Most Common Venue  \
0   Fried Chicken Joint              Breakfast Spot           Gas Station   
1              Pharmacy               Train Station            Restaurant   
2         Women's Store  Financial or Legal Service               Exhibit   
3     Fish & Chips Shop                     Exhibit            Eye Doctor   
4            Bagel Shop          Athletics & Sports           Supermarket   

       9th Most Common Venue 10th Most Common Venue  
0                 Bike Trail   Fast Food Restaurant  
1                        Bar                  Diner  
2                 Eye Doctor                Factory  
3                    Factory     Falafel Restaurant  
4  Middle Eastern Restaurant  Outdoors & Recreation

In [46]:
# set number of clusters
kclusters = 5

newyork_grouped_clustering = newyork_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(newyork_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 2, 4, 4, 4, 0, 0, 0, 0, 2], dtype=int32)

In [47]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

newyork_merged = neighborhoods

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
newyork_merged = newyork_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

newyork_merged.head() # check the last columns!

Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0   Bronx    Wakefield  40.894705 -73.847201               2   
1   Bronx   Co-op City  40.874294 -73.829939               2   
2   Bronx  Eastchester  40.887556 -73.827806               2   
3   Bronx    Fieldston  40.895437 -73.905643               0   
4   Bronx    Riverdale  40.890834 -73.912585               0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0              Pharmacy                  Food            Laundromat   
1        Baseball Field           Post Office           Pizza Place   
2  Caribbean Restaurant         Deli / Bodega           Bus Station   
3  Medical Supply Store           Bus Station                 Plaza   
4                  Park           Bus Station        Baseball Field   

  4th Most Common Venue 5th Most Common Venue       6th Most Common Venue  \
0         Deli / Bodega            Donut Shop              Sandwich Place   
1              Pharmacy    Salon / Barbershop                  Bagel Shop   
2                 Diner           Pizza Place        Fast Food Restaurant   
3                 River         Women's Store  Financial or Legal Service   
4                  Bank  Medical Supply Store                       Plaza   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0          Dessert Shop        Ice Cream Shop           Pizza Place   
1            Restaurant           Supermarket  Fast Food Restaurant   
2         Bowling Alley            Donut Shop     Convenience Store   
3               Exhibit            Eye Doctor               Factory   
4                   Gym   Filipino Restaurant            Eye Doctor   

  10th Most Common Venue  
0            Gas Station  
1          Grocery Store  
2      Food & Drink Shop  
3     Falafel Restaurant  
4                Factory

In [48]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(newyork_merged['Latitude'], newyork_merged['Longitude'], newyork_merged['Neighborhood'], newyork_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [50]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 0, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood      1st Most Common Venue  \
3                    Fieldston       Medical Supply Store   
4                    Riverdale                       Park   
9               Williamsbridge       Caribbean Restaurant   
12                 City Island            Harbor / Marina   
22                 Port Morris     Furniture / Home Store   
27                Clason Point                       Park   
28                 Throgs Neck         Italian Restaurant   
34                     Belmont         Italian Restaurant   
39              Edgewater Park         Italian Restaurant   
46                   Bay Ridge         Italian Restaurant   
47                 Bensonhurst         Chinese Restaurant   
49                  Greenpoint                        Bar   
50                   Gravesend         Italian Restaurant   
51              Brighton Beach                      Beach   
52              Sheepshead Bay               Dessert Shop   
57                  Kensington            Thai Restaurant   
58             Windsor Terrace              Deli / Bodega   
59            Prospect Heights                        Bar   
61                Williamsburg                        Bar   
62                    Bushwick                        Bar   
63          Bedford Stuyvesant                Coffee Shop   
64            Brooklyn Heights         Italian Restaurant   
65                 Cobble Hill                 Playground   
66             Carroll Gardens         Italian Restaurant   
67                    Red Hook                Art Gallery   
68                     Gowanus         Italian Restaurant   
69                 Fort Greene         Italian Restaurant   
70                  Park Slope                Coffee Shop   
76                 Mill Island                  Locksmith   
78                Coney Island           Baseball Stadium   
81               Dyker Heights               Dance Studio   
82             Gerritsen Beach                        Bar   
84                Clinton Hill                Pizza Place   
85                    Sea Gate                Sports Club   
86                    Downtown                Coffee Shop   
87                 Boerum Hill               Dance Studio   
88   Prospect Lefferts Gardens                     Bakery   
91                Bergen Beach            Harbor / Marina   
95           East Williamsburg                        Bar   
96                  North Side                Coffee Shop   
97                  South Side                        Bar   
98               Ocean Parkway           Sushi Restaurant   
99               Fort Hamilton              Deli / Bodega   
100                  Chinatown         Chinese Restaurant   
101         Washington Heights                       Café   
102                     Inwood         Mexican Restaurant   
103           Hamilton Heights                Pizza Place   
104             Manhattanville                Coffee Shop   
105             Central Harlem         African Restaurant   
106                East Harlem         Mexican Restaurant   
107            Upper East Side         Italian Restaurant   
108                  Yorkville         Italian Restaurant   
109                 Lenox Hill                Coffee Shop   
110           Roosevelt Island              Deli / Bodega   
111            Upper West Side         Italian Restaurant   
112             Lincoln Square                       Café   
113                    Clinton         Italian Restaurant   
114                    Midtown                Coffee Shop   
115                Murray Hill          Korean Restaurant   
116                    Chelsea                Coffee Shop   
117          Greenwich Village         Italian Restaurant   
118               East Village                        Bar   
119            Lower East Side                Art Gallery   
120                    Tribeca         Italian Restaurant   
121               Little Italy                     Ba

In [51]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 1, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
192   Somerville                  Park         Women's Store   
203    Todt Hill                  Park         Women's Store   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
192         Event Service               Exhibit            Eye Doctor   
203         Event Service               Exhibit            Eye Doctor   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
192               Factory    Falafel Restaurant                  Farm   
203               Factory    Falafel Restaurant                  Farm   

    9th Most Common Venue 10th Most Common Venue  
192        Farmers Market   Fast Food Restaurant  
203        Farmers Market   Fast Food Restaurant

In [52]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 2, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood      1st Most Common Venue  \
0               Wakefield                   Pharmacy   
1              Co-op City             Baseball Field   
2             Eastchester       Caribbean Restaurant   
5             Kingsbridge                Pizza Place   
6             Marble Hill                        Gym   
8                 Norwood                Pizza Place   
10             Baychester                 Donut Shop   
11         Pelham Parkway         Italian Restaurant   
13           Bedford Park         Chinese Restaurant   
14     University Heights                Pizza Place   
15         Morris Heights              Deli / Bodega   
16                Fordham          Mobile Phone Shop   
17           East Tremont                Pizza Place   
18             West Farms                Bus Station   
19           High  Bridge                   Pharmacy   
20                Melrose                Pizza Place   
21             Mott Haven                        Gym   
23               Longwood                      Diner   
24            Hunts Point                       Café   
25             Morrisania             Discount Store   
26              Soundview         Chinese Restaurant   
29           Country Club             Sandwich Place   
30            Parkchester                Pizza Place   
31     Westchester Square       Fast Food Restaurant   
33            Morris Park                Pizza Place   
35         Spuyten Duyvil               Intersection   
36        North Riverdale                Pizza Place   
37             Pelham Bay         Italian Restaurant   
38          Schuylerville                   Pharmacy   
40            Castle Hill                       Park   
41              Olinville                Supermarket   
42         Pelham Gardens                Pizza Place   
43              Concourse              Grocery Store   
44              Unionport                 Donut Shop   
45               Edenwald                Fish Market   
48            Sunset Park  Latin American Restaurant   
53      Manhattan Terrace         Chinese Restaurant   
54               Flatbush         Mexican Restaurant   
55          Crown Heights                Pizza Place   
56          East Flatbush                 Print Shop   
60            Brownsville                 Restaurant   
71          Cypress Hills        Fried Chicken Joint   
72          East New York              Deli / Bodega   
73          Starrett City       Caribbean Restaurant   
75              Flatlands                   Pharmacy   
79             Bath Beach                   Pharmacy   
80           Borough Park                       Bank   
83            Marine Park         Athletics & Sports   
90              City Line                 Donut Shop   
92                Midwood                Pizza Place   
93    Prospect Park South              Grocery Store   
94             Georgetown                       Bank   
133          Howard Beach         Italian Restaurant   
134                Corona                Supermarket   
136           Kew Gardens         Chinese Restaurant   
137         Richmond Hill              Deli / Bodega   
141         East Elmhurst                 Donut Shop   
142               Maspeth                      Diner   
143             Ridgewood              Deli / Bodega   
145             Rego Park                     Bakery   
146             Woodhaven              Deli / Bodega   
147            Ozone Park                Pizza Place   
149         College Point              Deli / Bodega   
154            Douglaston              Deli / Bodega   
155             Glen Oaks             Clothing Store   
156             Bellerose              Deli / Bodega   
157     Kew Gardens Hills                       Bank   
158         Fresh Meadows                Bus Station   
160        Jamaica Center          Mobile Phone Shop   
161       Oakland Gardens          Korean Restaurant   
162        Queens Village            

In [53]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 3, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
257  Howland Hook         Boat or Ferry         Women's Store   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
257           Fish Market               Exhibit            Eye Doctor   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
257               Factory    Falafel Restaurant                  Farm   

    9th Most Common Venue 10th Most Common Venue  
257        Farmers Market   Fast Food Restaurant

In [54]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 4, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
7            Woodlawn         Deli / Bodega                   Pub   
32           Van Nest         Deli / Bodega           Pizza Place   
74           Canarsie      Asian Restaurant         Deli / Bodega   
77    Manhattan Beach              Bus Stop       Harbor / Marina   
89         Ocean Hill         Deli / Bodega              Bus Stop   
144          Glendale           Pizza Place         Deli / Bodega   
148  South Ozone Park                  Park         Deli / Bodega   
150        Whitestone          Dance Studio           Candy Store   
159         Briarwood         Deli / Bodega            Playground   
171     Broad Channel         Deli / Bodega   Sporting Goods Shop   
193        Brookville         Deli / Bodega         Women's Store   
195      North Corona         Deli / Bodega           Pizza Place   
198      New Brighton              Bus Stop                  Park   
202       Grymes Hill               Dog Run              Bus Stop   
204       South Beach         Deli / Bodega                 Beach   
205     Port Richmond              Bus Stop           Pizza Place   
206  Mariner's Harbor    Italian Restaurant         Deli / Bodega   
210            Travis                 Hotel         Deli / Bodega   
212           Oakwood                Lawyer        Nightlife Spot   
217       Tottenville    Italian Restaurant        Cosmetics Shop   
224         Park Hill    Athletics & Sports              Bus Stop   
226      Graniteville              Bus Stop         Boat or Ferry   
227         Arlington          Intersection         Deli / Bodega   
228          Arrochar    Italian Restaurant              Bus Stop   
232     Midland Beach                 Beach            Restaurant   
234    New Dorp Beach    Italian Restaurant         Deli / Bodega   
241     Arden Heights         Deli / Bodega              Bus Stop   
245        Bloomfield          Burger Joint     Recreation Center   
252       Shore Acres    Italian Restaurant              Bus Stop   
254           Concord         Deli / Bodega    Athletics & Sports   
256     Randall Manor         Deli / Bodega                  Park   
258          Elm Park         Deli / Bodega    Italian Restaurant   
264            Utopia         Deli / Bodega            Playground   
285       Willowbrook    Chinese Restaurant         Deli / Bodega   
288           Roxbury             Irish Pub         Deli / Bodega   
295     Highland Park         Deli / Bodega    Spanish Restaurant   
305         Fox Hills          Cocktail Bar              Bus Stop   

    3rd Most Common Venue            4th Most Common Venue  \
7              Playground                      Pizza Place   
32               Bus Line                      Bus Station   
74   Caribbean Restaurant                              Gym   
77             Playground                   Sandwich Place   
89     Chinese Restaurant  Southern / Soul Food Restaurant   
144               Brewery                Food & Drink Shop   
148                   Bar                            Hotel   
150       Bubble Tea Shop                    Deli / Bodega   
159           Coffee Shop              Arts & Crafts Store   
171              Dive Bar                      Pizza Place   
193           Fish Market                          Exhibit   
195  Gym / Fitness Center                           Bakery   
198         Deli / Bodega                   Discount Store   
202           Fish Market                          Exhibit   
204                  Pier               Athletics & Sports   
205         Deli / Bodega                   Breakfast Spot   
206           Supermarket               Athletics & Sports   
210         Bowling Alley                              Gym   
212              Bus Stop                    Women's Store   
217    Mexican Restaurant                         Bus Stop   
224                 Hotel                      Coffee Shop   
226         Grocery St